In [16]:
# IMPORTS: Consolidated all import statements at the top for clarity and organization
import folium
from folium.plugins import HeatMap, MarkerCluster
from branca.element import MacroElement
from jinja2 import Template
from branca.colormap import linear
import geopandas as gpd
import pandas as pd
import numpy as np
from scipy.spatial import cKDTree
from shapely.geometry import Point
import warnings
from prophet import Prophet
import matplotlib.pyplot as plt
from statsmodels.tsa.seasonal import seasonal_decompose


# Suppress future warnings: Helps reduce noise in output logs from future library updates
warnings.filterwarnings("ignore", category=FutureWarning)

# Suppress deprecation warnings: Ignore warnings related to deprecated features
warnings.filterwarnings("ignore", category=DeprecationWarning)

# Setting pandas display options: Ensures that dataframes display all rows, columns, and full cell contents in the output
pd.set_option('display.max_colwidth', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)


In [2]:
# Load the dataset
df_incident = pd.read_csv('incident_cleaned_final.csv', low_memory=False)

# Convert incident datetime columns to datetime format
df_incident['incident_date_time'] = pd.to_datetime(df_incident['incident_date_time'])
df_incident['datetimealarm'] = pd.to_datetime(df_incident['datetimealarm'])
df_incident['datetimearr'] = pd.to_datetime(df_incident['datetimearr'])


In [3]:
# Display the first few rows for inspection
df_incident.head()


incident_number  incident_date_time             incident_address  \
0           131453 2022-07-11 04:46:25         CHILI AVE & CAIRN ST   
1           135415 2022-07-26 22:17:08           1600 LEXINGTON AVE   
2           144243 2022-08-31 21:10:43       BLOSSOM RD & RT 590 NB   
3           156371 2022-10-16 20:45:02               292 HUDSON AVE   
4           156395 2022-10-16 22:36:23  S CLINTON AVE & AVERILL AVE   

          street cross_street       city state    zip  sitfound  \
0      CHILI AVE     CAIRN ST  Rochester    NY  14624     611.0   
1  LEXINGTON AVE      Unknown     Greece    NY  14606     611.0   
2     BLOSSOM RD    RT 590 NB   Brighton    NY  14610     611.0   
3     HUDSON AVE   HOLLAND ST  Rochester    NY  14605     743.0   
4  S CLINTON AVE  AVERILL AVE  Rochester    NY  14620     321.0   

                                  incident_type_descr inctype_grouped_descr  \
0                      Dispatched & canceled en route           Good Intent   
1                      Dispatched & canceled en route           Good Intent   
2                      Dispatched & canceled en route           Good Intent   
3  Smoke detector activation, no fire - unintentional           False Calls   
4    EMS call, excluding vehicle accident with injury          Rescue & EMS   

   expnum primary_unit all_units       datetimealarm         datetimearr  \
0       0        CAR45     CAR45 2022-07-11 04:46:25 2022-07-11 04:50:52   
1       0        CAR45     CAR45 2022-07-26 22:17:08 2022-07-26 22:21:35   
2       0           T4        T4 2022-08-31 21:10:43 2022-08-31 21:13:04   
3       0        CAR45     CAR45 2022-10-16 20:45:02 2022-10-16 20:53:22   
4       0        CAR45     CAR45 2022-10-16 22:36:23 2022-10-16 22:40:15   

   evlength  schdshiftname_code      CAD_num  loctype_code   loctype_descr  \
0      0.24                 3.0  E2219200393             2    Intersection   
1      0.24                 1.0  E2220703097             1  Street address   
2      0.44                 1.0  E2224303031             2    Intersection   
3      0.24                 4.0  E2228902396             1  Street address   
4      0.24                 4.0  E2228902598             2    Intersection   

  schdshiftname_descr  alarmnum  fire_service_deaths  civilian_deaths  \
0             Group 3       1.0                  0.0              0.0   
1             Group 1       1.0                  0.0              0.0   
2             Group 1       1.0                  0.0              0.0   
3             Group 4       1.0                  0.0              0.0   
4             Group 4       1.0                  0.0              0.0   

   fire_service_injuries  civilian_injuries oic_assignment  \
0                    0.0                0.0   Unit Officer   
1                    0.0                0.0   Unit Officer   
2                    0.0                0.0   Unit Officer   
3                    0.0                0.0   Unit Officer   
4                    0.0                0.0   Unit Officer   

           oic_signed_date  PERSIDMAKEREP memrep_rank memrep_assignment  \
0  2022-12-06 00:00:00.000         1373.0  Lieutenant      Unit Officer   
1  2022-12-06 00:00:00.000         1373.0  Lieutenant      Unit Officer   
2  2022-09-02 00:00:00.000         1220.0  Lieutenant      Unit Officer   
3  2023-02-08 00:00:00.000         1373.0     Captain      Unit Officer   
4  2023-02-08 00:00:00.000         1373.0     Captain      Unit Officer   

  primary_agency                                 caller_address  \
0          28008  966 CHILI AVE              S SECTOR ROCHESTER   
1          28008                                        Unknown   
2          28008       444 BROWNCROFT BL          SW SECTOR BRI   
3          28008               287 N UNION ST             W ROC   
4          28008          919 CLINTON AVE S - NW SECT ROCHESTER   

   time_to_reach USER_CAD_num        USER_incident_address  USER_zip  \
0         4.4500  E2219200393     

In [4]:
# Create GeoDataFrame for incident data
gdf_incident = gpd.GeoDataFrame(
    df_incident,
    geometry=gpd.points_from_xy(df_incident['longitude'], df_incident['latitude']),
    crs='EPSG:4326'
)


In [5]:
# Load fire station shapefile
shapefile_path = "RFD_Station_Locations.shp"
gdf_fire_stations = gpd.read_file(shapefile_path)

In [6]:
# Ensure geometry column exists for fire stations
if 'geometry' not in gdf_fire_stations.columns:
    gdf_fire_stations['geometry'] = gpd.points_from_xy(gdf_fire_stations['longitude'], gdf_fire_stations['latitude'])
    gdf_fire_stations.set_crs(epsg=4326, inplace=True)


In [7]:
# Select only necessary columns for incident GeoDataFrame
gdf_incident = gdf_incident[['incident_number', 'incident_date_time', 'zip', 'sitfound',
                             'incident_type_descr', 'inctype_grouped_descr', 'primary_unit', 'all_units',
                             'datetimealarm', 'datetimearr', 'evlength', 'time_to_reach',
                             'latitude', 'longitude', 'geometry', 'nearest_station_name', 'response_station_name']]


In [8]:
# Load ZIP code shapefile
zip_file_path = "tl_2024_us_zcta520.shp"
gdf_zip = gpd.read_file(zip_file_path)


In [9]:
# Ensure ZIP code GeoDataFrame uses the correct CRS
if gdf_zip.crs != "EPSG:4326":
    gdf_zip = gdf_zip.to_crs(epsg=4326)


In [10]:
# Rename ZIP code column for consistency
gdf_zip = gdf_zip.rename(columns={"ZCTA5CE20": "ZIP"})


In [11]:
# Convert ZIP codes to string for both datasets
gdf_incident['zip'] = gdf_incident['zip'].astype(str)
gdf_zip['ZIP'] = gdf_zip['ZIP'].str[:5]


In [12]:
# Filter ZIP codes to only those shared between datasets
common_zips = set(gdf_incident['zip']).intersection(set(gdf_zip['ZIP']))
gdf_zip = gdf_zip[gdf_zip['ZIP'].isin(common_zips)]


# Map1. Average Response Time and Incident Analysis by ZIP (2019-2024)

In [20]:
# Map 1: Average Response Time and Incident Analysis by ZIP
def add_response_time_legend(map_obj):
    legend_html = """
    <div style="position: fixed; 
                bottom: 50px; left: 50px; width: 250px; height: 100px; 
                background-color: white; z-index:1000; font-size:14px;
                border:2px solid gray; padding: 10px;">
        <b>Response Time Threshold:</b><br>
        <span style="color: red;">5 minutes</span> or less is the target.<br>
        Areas exceeding this time are critical.
    </div>
    """
    map_obj.get_root().html.add_child(folium.Element(legend_html))

def create_combined_map_with_adjustments2(gdf_incident, gdf_zip, gdf_fire_stations):
    # Filter for the last five years (2019–2024)
    gdf_incident['incident_date_time'] = pd.to_datetime(gdf_incident['incident_date_time'])
    filtered_incidents = gdf_incident[gdf_incident['incident_date_time'].dt.year >= 2019]

    # Transform coordinate systems if necessary
    if gdf_zip.crs != "EPSG:4326":
        gdf_zip = gdf_zip.to_crs(epsg=4326)
    if gdf_fire_stations.crs != "EPSG:4326":
        gdf_fire_stations = gdf_fire_stations.to_crs(epsg=4326)

    # Rename ZIP Code column if necessary
    if "ZCTA5CE20" in gdf_zip.columns:
        gdf_zip = gdf_zip.rename(columns={"ZCTA5CE20": "ZIP"})

    # Aggregate data by ZIP Code
    avg_time = gdf_incident.groupby('zip')['time_to_reach'].median().reset_index()
    total_incidents_by_zip = gdf_incident.groupby('zip').size().reset_index(name='total_incidents')
    gdf_zip = gdf_zip.merge(avg_time, left_on='ZIP', right_on='zip', how='left')
    gdf_zip = gdf_zip.merge(total_incidents_by_zip, left_on='ZIP', right_on='zip', how='left')

    # Calculate the total number of incidents
    total_incidents = len(gdf_incident)
    gdf_zip['incident_percentage'] = (gdf_zip['total_incidents'] / total_incidents * 100).round(1)

    # Create the map
    combined_map = folium.Map(location=[gdf_incident['latitude'].mean(), gdf_incident['longitude'].mean()], zoom_start=12)

    # Add a choropleth map
    folium.Choropleth(
        geo_data=gdf_zip,
        data=gdf_zip,
        columns=['ZIP', 'time_to_reach'],
        key_on='feature.properties.ZIP',
        fill_color='YlOrRd',
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name='Average Time to Reach (mins)',
        bins=[0, 4, 5, 6, 7, 8, 9, 10],
        nan_fill_color='gray'
    ).add_to(combined_map)

    # Add tooltips for ZIP Code areas
    folium.GeoJson(
        gdf_zip,
        style_function=lambda x: {
            'fillColor': 'transparent',  # Keep choropleth fill
            'color': 'gray',  # Gray border
            'weight': 0.5,  # Border width
            'fillOpacity': 0.5  # Transparency for the fill
        },
        tooltip=folium.GeoJsonTooltip(
            fields=['ZIP', 'time_to_reach', 'total_incidents', 'incident_percentage'],
            aliases=[
                'Zip Code:', 
                'Avg Time to Reach (mins):', 
                'Total Incidents:', 
                'Incident Percentage (%):'
            ],
            localize=True,
            labels=True
        ),
        highlight_function=lambda x: {
            'fillOpacity': 0.5,
            'weight': 0,
            'color': 'transparent'
        }
    ).add_to(combined_map)

    # Add markers for fire stations
    for _, station in gdf_fire_stations.iterrows():
        # Filter incidents related to each station
        station_incidents = gdf_incident[gdf_incident['nearest_station_name'] == station['NAME']]
        station_total = len(station_incidents)
        station_percentage = (station_total / total_incidents) * 100 if total_incidents > 0 else 0

        # Calculate incident type percentages
        incident_counts = station_incidents['inctype_grouped_descr'].value_counts()
        incident_percentages = (incident_counts / station_total * 100).round(1)

        # Create popup content
        popup_html = f"<b>{station['NAME']}</b><br>"
        popup_html += f"<b>Total Incidents: {station_total:,}</b> <span style='color: gray;'>({station_percentage:.1f}%)</span><br>"
        for incident_type, count in incident_counts.items():
            percentage = incident_percentages[incident_type]
            popup_html += f"<b>{incident_type}:</b> {count:,} <span style='color: gray;'>({percentage:.1f}%)</span><br>"

        # Add marker to the map
        folium.Marker(
            location=[station['latitude'], station['longitude']],
            popup=folium.Popup(popup_html, max_width=300),
            icon=folium.Icon(icon='fire', prefix='fa', color='red')
        ).add_to(combined_map)

    # Add ZIP Code labels
    for _, row in gdf_zip.iterrows():
        if not pd.isna(row['ZIP']):
            folium.map.Marker(
                [row['geometry'].centroid.y, row['geometry'].centroid.x],
                icon=folium.DivIcon(
                    html=f"""<div style="font-size: 8px; color: gray; font-weight: normal;">{row['ZIP']}</div>"""
                )
            ).add_to(combined_map)

    # Add response time legend
    add_response_time_legend(combined_map)

    return combined_map

# Generate Map 1
map_average_response_time = create_combined_map_with_adjustments2(gdf_incident, gdf_zip, gdf_fire_stations)
map_average_response_time.save("Map1_Average_Response_Time_and_Incident_Analysis_by_ZIP_2019-2024.html")


In [21]:
map_average_response_time

# Map2. Incident Type Distribution and Fire Station Workload (2019-2024)

In [24]:
def create_map_with_fire_station_details(gdf_incident, gdf_zip, gdf_fire_stations):
    # Filter for the last five years (2019–2024)
    gdf_incident['incident_date_time'] = pd.to_datetime(gdf_incident['incident_date_time'])
    filtered_incidents = gdf_incident[gdf_incident['incident_date_time'].dt.year >= 2019]

    # Ensure the coordinate system is correct
    if gdf_zip.crs != "EPSG:4326":
        gdf_zip = gdf_zip.to_crs(epsg=4326)
    if gdf_fire_stations.crs != "EPSG:4326":
        gdf_fire_stations = gdf_fire_stations.to_crs(epsg=4326)

    # Calculate incident type counts and percentages by ZIP
    incident_type_counts = gdf_incident.groupby(['zip', 'inctype_grouped_descr']).size().unstack(fill_value=0)
    incident_type_percentages = incident_type_counts.div(incident_type_counts.sum(axis=0), axis=1) * 100

    # Merge the calculated percentages with the ZIP GeoDataFrame
    gdf_zip = gdf_zip.merge(incident_type_percentages, left_on='ZIP', right_index=True, how='left').fillna(0)

    # Round percentages to two decimal places for better readability
    for column in incident_type_percentages.columns:
        gdf_zip[column] = gdf_zip[column].round(2)

    # Create the map
    map_with_fire_stations = folium.Map(location=[gdf_incident['latitude'].mean(), gdf_incident['longitude'].mean()],
                                        zoom_start=12)

    # Add a title at the top of the map
    title_html = '''
         <div style="position: fixed; 
                     top: 10px; left: 50px; width: 90%; height: auto; 
                     background-color: white; z-index: 1000; font-size: 16px; 
                     border: 2px solid black; padding: 10px; text-align: center;">
             <b>Fire Stations and Incident Types by ZIP Code</b>
         </div>
     '''
    map_with_fire_stations.get_root().html.add_child(folium.Element(title_html))

    # Add an improved color scale: OrRd (Red/Orange theme)
    colormap = linear.OrRd_09.scale(0, 30)  # Cap the percentage scale at 30% for better contrast
    colormap.caption = "Incident Type Percentage (%)"
    map_with_fire_stations.add_child(colormap)

    # Add GeoJson layers for each incident type
    for incident_type in incident_type_percentages.columns:
        feature_group = folium.FeatureGroup(name=f"{incident_type} (%)")

        # Style the GeoJson layer
        folium.GeoJson(
            gdf_zip,
            style_function=lambda x, incident_type=incident_type: {
                'fillColor': colormap(min(x['properties'].get(incident_type, 0), 30)),  # Cap at 30%
                'color': 'black',
                'weight': 0.5,
                'fillOpacity': 0.8 if x['properties'].get(incident_type, 0) > 0 else 0,
            },
            tooltip=folium.GeoJsonTooltip(
                fields=['ZIP', incident_type],
                aliases=['Zip Code:', f'{incident_type} %:'],
                localize=True,
                labels=True
            )
        ).add_to(feature_group)

        feature_group.add_to(map_with_fire_stations)

    # Add fire station markers with detailed information
    total_incidents = len(gdf_incident)
    for _, station in gdf_fire_stations.iterrows():
        # Filter incidents related to each fire station
        station_incidents = gdf_incident[gdf_incident['nearest_station_name'] == station['NAME']]
        station_total = len(station_incidents)
        station_percentage = (station_total / total_incidents * 100) if total_incidents > 0 else 0

        # Calculate incident type percentages for the station
        incident_counts = station_incidents['inctype_grouped_descr'].value_counts()
        incident_percentages = (incident_counts / station_total * 100).round(1)

        # Create popup content for the fire station
        popup_html = f"<b>{station['NAME']}</b><br>"
        popup_html += f"<b>Total Incidents: {station_total:,}</b> <span style='color: gray;'>({station_percentage:.1f}%)</span><br>"
        for incident_type, count in incident_counts.items():
            percentage = incident_percentages[incident_type]
            popup_html += f"<b>{incident_type}:</b> {count:,} <span style='color: gray;'>({percentage:.1f}%)</span><br>"

        # Add a fire station marker
        folium.Marker(
            location=[station['latitude'], station['longitude']],
            popup=folium.Popup(popup_html, max_width=300),
            icon=folium.Icon(icon='fire', prefix='fa', color='red')
        ).add_to(map_with_fire_stations)

        # Add a station name label slightly offset from the marker
        folium.Marker(
            location=[station['latitude'] + 0.0003, station['longitude']],  # Slight offset for better positioning
            icon=folium.DivIcon(html=f'''
                <div style="
                    font-size: 10px; 
                    font-weight: bold; 
                    color: white; 
                    background-color: rgba(0, 0, 0, 0.5);  /* Semi-transparent black */
                    padding: 2px 10px;  /* Increase horizontal padding */
                    border-radius: 4px; 
                    text-align: center; 
                    white-space: nowrap;  /* Prevent text wrapping */
                    min-width: 50px;  /* Set a minimum width for consistency */
                    display: inline-block;">
                    {station['NAME']}
                </div>
            ''')
        ).add_to(map_with_fire_stations)

    # Add ZIP Code labels
    for _, row in gdf_zip.iterrows():
        if not pd.isna(row['ZIP']):  # Only add labels for valid ZIP codes
            folium.Marker(
                location=[row['geometry'].centroid.y, row['geometry'].centroid.x],
                icon=folium.DivIcon(html=f'<div style="font-size: 7px; color: black; font-weight: normal;">{row["ZIP"]}</div>')
            ).add_to(map_with_fire_stations)

    # Add layer control for toggling incident type layers
    folium.LayerControl(collapsed=False).add_to(map_with_fire_stations)

    return map_with_fire_stations

# Generate and save Map 2
map_incident_distribution = create_map_with_fire_station_details(gdf_incident, gdf_zip, gdf_fire_stations)
map_incident_distribution.save("Map2_Incident_Type_Distribution_and_Fire_Station_Workload_2019-2024.html")


In [25]:
map_incident_distribution